In [23]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [24]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import copy
import yaml
import datetime
from typing import Tuple, Dict

from simulator import *
from load_data import load_md_from_file
from stoikov import StoikovStrategy
# from get_info import get_metrics, md_to_dataframe
from get_info import get_metrics, md_to_dataframe

In [25]:
MARKET_DATA_PATH = '../md/btcusdt:Binance:LinearPerpetual/'

# Stoikov strategy

Article: [Stoikov 2008] Avellaneda, M., & Stoikov, S. (2008). High-frequency trading in a limit order book. Quantitative Finance, 8(3), 217-224.

**1. Reservation price**
$$ r(s, t) = s - q \gamma \sigma^2 (T-t). $$

- $s$ is mid-price.
- $q$ is position size in base asset.
- $T$ is terminal time.
- $t$ is current time.
- $\sigma$ is volatiliaty of standard Brownian motion ($dS = \sigma dW$), by which the price is modeled in this article.
- $\gamma$ -- risk aversity.

$\sigma$ and $\gamma$ are parameters of the strategy.

**2. Spread**

$$ \delta^a + \delta^b = \gamma\sigma^2(T-t) + \frac{2}{\gamma} \log\left(1 + \frac{\gamma}{k}\right).$$

Here $k = \alpha K$, where
- $\alpha$ is from $f^Q(x) \propto x^{-1-\alpha}$ -- density of market order size (formula 9 from [Stoikov 2008]);
- $K$ is from $\Delta p \propto K^{-1} \log(Q)$ (formulas 11, 12 from [Stoikov 2008]).

# [Optional] Calculate parameter $\sigma$

# Backtesting functions

In [26]:
def my_round(x, ndigits):
    return round(float(x), ndigits)

def get_metrics_numeric(metrics):
    metrics_numeric = {
        'Final PnL':    my_round(metrics['total'].iloc[-1], 2),
        'Final volume': my_round(metrics['BTC'].iloc[-1], 3),
    }
    return metrics_numeric

def backtest(md, sim_params: dict, strat_params: dict, fee: float) -> Tuple[pd.DataFrame, Dict]:
    """Run backtest and return results.
    Args:
        md: Parameter `md` (market data) for `Sim` constructor.
        sim_params: All parameters for `Sim` constructor, except `md`
        strat_params: All parameters for StoikovStrategy constructor, except `sim`.
        fee: Parameter `fee` for `get_metrics()` function.
    Returns:
        Simulation metrics in form of time series and single quantities.
    """
    sim = Sim(md, **sim_params)
    strategy = StoikovStrategy(sim, **strat_params)
    trades_list, md_list, updates_list, all_orders = strategy.run()
    metrics = get_metrics(updates_list, fee=fee)
    metrics_numeric = get_metrics_numeric(metrics)
    return metrics, metrics_numeric

In [27]:
def plot_metrics(metrics, metrics_numeric, asset, title=''):
    """Visualize backtesting results"""
    fig = make_subplots(rows=5, cols=1, row_heights=[0.3, 0.3, 0.2, 0.2, 0.2], shared_xaxes=True, vertical_spacing=0.005)
    fig.add_trace(go.Scatter(
        name='PnL',
        x=metrics['receive_ts'],
        y=metrics['total'],
        line=dict(color=px.colors.qualitative.Plotly[0]),
        showlegend=False
    ), row=1, col=1)

    fig.add_trace(go.Scatter(
        name='Mid-price',
        x=metrics['receive_ts'],
        y=metrics['mid_price'],
        line=dict(color=px.colors.qualitative.Plotly[5]),
        showlegend=False
    ), row=2, col=1)

    fig.add_trace(go.Scatter(
        name='Volume',
        x=metrics['receive_ts'],
        y=metrics['BTC'],
        line=dict(color=px.colors.qualitative.Plotly[2]),
        showlegend=False
    ), row=3, col=1)


    metrics_numeric_txt = yaml.dump(metrics_numeric, default_flow_style=False, sort_keys=False).replace('\n', '<br>')
    fig.add_annotation(text=metrics_numeric_txt,
                       xref='paper', yref='paper', x=1, y=0.9,
                       align='left', font={'family': 'monospace'})

    time_str = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    title += f'<br>Backtest on {asset}' \
             f'<br>Launch time: {time_str}'

    fig.update_layout(width=1000, height=1400,
                      title=title, xaxis5_title='Receive time',
                      yaxis1_title='PnL (account worth in quote asset)', yaxis2_title='Mid-price',
                      yaxis3_title='Trade volume', yaxis4_title='Base asset balance',
                      yaxis5_title='Quote asset balance')
    fig.update_traces(xaxis='x5')
    fig.update_xaxes(showspikes=True, spikemode='across', spikedash='dot', spikethickness=2)
    fig.update_yaxes(showspikes=True, spikemode='across', spikedash='dot', spikethickness=2)
    return fig

# Run the backtesting

In [28]:
T = pd.Timedelta(50, 'm').delta
md = load_md_from_file(MARKET_DATA_PATH, T)

/var/folders/0s/9ph2yzfj66q6rkt2s8_1fl7m0000gn/T/ipykernel_58153/2696025944.py:1: FutureWarning:

Timedelta.delta is deprecated and will be removed in a future version.



In [29]:
sim_params = {
    'execution_latency': 10_000_000,
    'md_latency': 10_000_000
}
strat_params = {
    'gamma': 2,
    'k': 0.8,  # calculated from BTCUSDT market data (see eda/eda-btc.ipynb)
    'sigma': 1,
    'terminal_time': False,
    'adjust_delay': 1_000_000,
    'order_size': 0.001,
    'min_order_size': 0.001,
    'precision': 2
}
FEE = 0.0

In [30]:
metrics, metrics_num = backtest(md, sim_params, {**strat_params, 'terminal_time': False}, fee=FEE)
plot_metrics(metrics[::60], metrics_num, asset='BTCUSDT', title='WITHOUT terminal time')

## Compare strategy with and without terminal time

In [12]:
sim_params = {
    'execution_latency': 10_000_000,
    'md_latency': 10_000_000
}
strat_params = {
    'gamma': 2,
    'k': 0.8,
    'sigma': 1,
    'terminal_time': None,
    'adjust_delay': 1_000_000,
    'order_size': 0.001,
    'min_order_size': 0.001,
    'precision': 2
}
FEE = 0.0

In [13]:
metrics_without, metrics_num_without = backtest(md, sim_params, {**strat_params, 'terminal_time': False}, fee=FEE)
plot_metrics(metrics_without[::60], metrics_num_without, asset='BTCUSDT', title='WITHOUT terminal time')

In [21]:
metrics_with, metrics_num_with = backtest(md, sim_params, {**strat_params, 'terminal_time': True}, fee=FEE)
plot_metrics(metrics_with[::60], metrics_num_with, asset='BTCUSDT', title=f'WITH terminal time')

Without terminal time, strategy performance is stable in terms of balances in base and quote asset. Therefore, it is best not to use terminal time.

## Compare strategy performance with and without fees

In [15]:
sim_params = {
    'execution_latency': 10_000_000,
    'md_latency': 10_000_000
}
strat_params = {
    'gamma': 2,
    'k': 0.8,  # calculated from BTCUSDT market data (see eda/eda-btc.ipynb)
    'sigma': 1,
    'terminal_time': False,
    'adjust_delay': 1_000_000,
    'order_size': 0.001,
    'min_order_size': 0.001,
    'precision': 2
}

In [17]:
sim = Sim(md, **sim_params)
strategy = StoikovStrategy(sim, **strat_params)
_, _, updates_list, _ = strategy.run()

In [20]:
def test_for_fee(updates_list, fee):
    metrics = get_metrics(updates_list, fee=fee)
    metrics_numeric = get_metrics_numeric(metrics)
    fig = plot_metrics(metrics[::60], metrics_numeric, asset='BTCUSDT', title=f'fee: {fee*100}%')
    return fig

In [21]:
test_for_fee(updates_list, 0.0)

In [22]:
test_for_fee(updates_list, 0.0002)